Написать программу для построения обратного индекса с учетом морфологического анализа. Необходимо реализовать возможность поиска по нескольким словам.

In [7]:
import os
import pickle
import json
from tqdm import tqdm
import nltk
from nltk.corpus import stopwords
from nltk.stem.snowball import SnowballStemmer

from collections import defaultdict
from pymystem3 import Mystem


Lemmatizer = Mystem()
Stemmer = SnowballStemmer("russian")


def lemmatize_sentence(text):
    lemmas = Lemmatizer.lemmatize(text)
    return "".join(lemmas).strip()


def tokenize_text(text, lemmatize=False, stem=False):
    if lemmatize:
        text = lemmatize_sentence(text)

    tokens = nltk.word_tokenize(text.lower())
    clean_tokens = [
        word
        for word in tokens
        if word.isalnum() and word not in stopwords.words("russian")
    ]

    if stem:
        clean_tokens = [Stemmer.stem(word) for word in clean_tokens]

    return clean_tokens


def build_inverted_index(texts, lemmatize, stem):
    inverted_index = defaultdict(list)

    for doc_id, text in tqdm(
        enumerate(texts), desc="Building inverted index", total=len(texts)
    ):
        if text is None:
            continue
        tokens = tokenize_text(text, lemmatize, stem)
        for token in set(tokens):
            inverted_index[token].append(doc_id)
    return inverted_index


def load_inverted_index(path, texts, lemmatize=False, stem=False):
    if os.path.exists(path):
        with open(path, "rb") as f:
            return pickle.load(f)
    else:
        result = build_inverted_index(texts, lemmatize, stem)
        with open(path, "wb") as f:
            pickle.dump(result, f)
        return result


def search(query, inverted_index, lemmatize=False, stem=False):
    query_tokens = set(tokenize_text(query, lemmatize, stem))
    search_results = set()

    for token in query_tokens:
        if token in inverted_index:
            if not search_results:
                search_results = set(inverted_index[token])
            else:
                search_results = search_results.intersection(set(inverted_index[token]))

    return search_results

In [8]:
with open("../naked_science_corpus.json", "r") as f:
    data = json.load(f)

texts = [article["text"] for article in data]

inverted_index = load_inverted_index("inverted_index.pickle", texts, lemmatize=True)

In [9]:
inverted_index

defaultdict(list,
            {'импульс': [0,
              6,
              10,
              22,
              110,
              193,
              230,
              235,
              259,
              305,
              311,
              333,
              337,
              430,
              477,
              591,
              633,
              685,
              691,
              712,
              762,
              803,
              834,
              860,
              929,
              932,
              969,
              1006,
              1040,
              1047,
              1074,
              1086,
              1146,
              1150,
              1170,
              1194,
              1198,
              1271,
              1355,
              1381,
              1390,
              1428,
              1453,
              1471,
              1477,
              1508,
              1535,
              1536,
              1551,
              1557,
    

In [5]:
query = "искуственный интеллект"
results = search(query, inverted_index)

print('Результаты поиска для запроса "{}":'.format(query))
for result in results:
    print(result, texts[result])

TypeError: argument of type 'NoneType' is not iterable

In [13]:
query = "ядерная физика"
results = search(query, inverted_index)

print('Результаты поиска для запроса "{}":'.format(query))
for result in results:
    print(result, texts[result])

Результаты поиска для запроса "ядерная физика":
2691 Британская версия событий: операция «Новичок». На Западе популярны целые книги, описывающие, как именно действия союзников лишили Третий рейх шансов на ядерную бомбу. Ключевая линия повествования там такая: для получения бомбы Гитлеру нужна была тяжелая вода (такая, где вместо обычного водорода тяжелый — дейтерий). Восемнадцатого октября 1942 года англичане сбросили четырех диверсантов передовой группы в районе норвежской фабрики по производству тяжелой воды (операция «Шотландская куропатка», традиционно ошибочно переводится как «Тетерев»). Туда же 19 ноября того же года на планерах должны были высадиться 34 диверсанта-англичанина из SAS (операция «Новичок», традиционно ошибочно переводится как «Незнакомец»). Два четырехмоторных самолета-буксира тащили два планера Airspeed AS.51 Horsa, где и размещались десантники. Один буксир потерял планер (обрыв троса) не там, где нужно было высадиться. Трое сасовцев погибли, остальных 14 немцы вс